# Equation Discovery with Symbolic Regression to Paramterize Heat Flux in the Atmospheric Boundary Layer

*Authors: Antony Sikorski*

This notebook should make it easy to perform equation discovery with the use of the function `discover_eqs`. 

This function uses a number of supporting functions from the accompanying `functions.py` file, and should output a dataframe of possible equations.

We use the `PySR` package for symbolic regression, an ML method for finding interpretable symbolic expressions.

In [1]:
#importing libraries
# from pdfs import *
import os
import re

import xarray as xr
import netCDF4 as nc
import h5netcdf

import numpy as np
import matplotlib.pyplot as plt
from IPython.display import display
import pandas as pd

import pysr
from pysr import PySRRegressor

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score

from functions import *

Detected IPython. Loading juliacall extension. See https://juliapy.github.io/PythonCall.jl/stable/compat/#IPython


Some quick data processing: 

In [2]:
path = 'C:/Users/anton/Desktop/Career/LEAP_nyc_Summer2024/les_sim_2/'

directories, items = list_directories_files(path)
print("Directories starting with 'Ug':", directories)
print("Files starting with 'Ug':", items)

Directories starting with 'Ug': []
Files starting with 'Ug': ['Ug16Q000_IV.nc', 'Ug16Q001_IV.nc', 'Ug16Q003_IV.nc', 'Ug16Q006_I.nc', 'Ug16Q006_IV.nc', 'Ug16Q010_IV.nc', 'Ug1Q01_II.nc', 'Ug2Q010_I.nc', 'Ug2Q010_IV.nc', 'Ug2Q01_III.nc', 'Ug2Q024_I.nc', 'Ug8Q003_II.nc', 'Ug8Q003_III.nc', 'Ug8Q003_IV.nc', 'Ug8Q006_IV.nc']


In [3]:
for item in items:
    ds_stat = nc.Dataset( os.path.join(path, item), mode='r')
    if 'budget' in ds_stat.groups:
        print ("budget is in", item)
    else:
        print ("budget is not in", item)

budget is not in Ug16Q000_IV.nc
budget is in Ug16Q001_IV.nc
budget is in Ug16Q003_IV.nc
budget is in Ug16Q006_I.nc
budget is in Ug16Q006_IV.nc
budget is in Ug16Q010_IV.nc
budget is in Ug1Q01_II.nc
budget is in Ug2Q010_I.nc
budget is in Ug2Q010_IV.nc
budget is in Ug2Q01_III.nc
budget is in Ug2Q024_I.nc
budget is in Ug8Q003_II.nc
budget is in Ug8Q003_III.nc
budget is in Ug8Q003_IV.nc
budget is in Ug8Q006_IV.nc


In [4]:
for item in items[1:]:
    print(item)
    df = nc.Dataset(path + '/' + item, mode='r')
    print(df)

Ug16Q001_IV.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF4 data model, file format HDF5):
    dimensions(sizes): z(384), zh(385), time(120)
    variables(dimensions): float64 time(time), float64 z(z), float64 zh(zh)
    groups: default, thermo, budget
Ug16Q003_IV.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF4 data model, file format HDF5):
    dimensions(sizes): z(384), zh(385), time(120)
    variables(dimensions): float64 time(time), float64 z(z), float64 zh(zh)
    groups: default, thermo, budget
Ug16Q006_I.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF4 data model, file format HDF5):
    dimensions(sizes): z(256), zh(257), time(120)
    variables(dimensions): float64 time(time), float64 z(z), float64 zh(zh)
    groups: default, thermo, budget
Ug16Q006_IV.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF4 data model, file format HDF5):
    dimensions(sizes): z(384), zh(385), time(90)
    variables(dimensions): float64 time(time), float64 z(z), f

In [5]:
target_z_dim = 384

selected_files = []

for item in items[1:]:
        df = nc.Dataset(os.path.join(path, item), mode='r')
        if df.dimensions['z'].size == target_z_dim:
            selected_files.append(item)
        df.close()


print("Total number of files: ", len(items))
print("Number of valid files (same z and zh dims): ", len(selected_files))
print("Valid files: ", selected_files)

Total number of files:  15
Number of valid files (same z and zh dims):  11
Valid files:  ['Ug16Q001_IV.nc', 'Ug16Q003_IV.nc', 'Ug16Q006_IV.nc', 'Ug16Q010_IV.nc', 'Ug1Q01_II.nc', 'Ug2Q010_IV.nc', 'Ug2Q01_III.nc', 'Ug8Q003_II.nc', 'Ug8Q003_III.nc', 'Ug8Q003_IV.nc', 'Ug8Q006_IV.nc']


In [6]:
#eqs_Ug16Q001_IV = discover_eqs(path, ['Ug16Q001_IV.nc'], time_avg = 15, indices = np.s_[:, 0:200], difficulty = "hard")

In [7]:
# eqs_Ug16Q001_IV

In [8]:
#eqs_Ug2Q010_IV = discover_eqs(path, ['Ug2Q010_IV.nc'], time_avg = 15, indices = np.s_[:, 0:200], difficulty = "hard")

In [9]:
# eqs_Ug2Q010_IV

In [10]:
eqs_easy_mm = discover_eqs(path, selected_files, time_avg = 15, indices = np.s_[:, 0:200], difficulty = "easy", normChoice = "zscore")
eqs_medium_mm = discover_eqs(path, selected_files, time_avg = 15, indices = np.s_[:, 0:200], difficulty = "medium", normChoice = "zscore")
eqs_mediumhard_mm = discover_eqs(path, selected_files, time_avg = 15, indices = np.s_[:, 0:200], difficulty = "mediumhard", normChoice = "zscore")
eqs_hard_mm = discover_eqs(path, selected_files, time_avg = 15, indices = np.s_[:, 0:200], difficulty = "hard", normChoice = "zscore")

Don't forget to unnormalize the coef (minmax)
Compiling Julia backend...


c:\Python\Python_3_11\Lib\site-packages\pysr\sr.py:65: UserWarning: You are using the `^` operator, but have not set up `constraints` for it. This may lead to overly complex expressions. One typical constraint is to use `constraints={..., '^': (-1, 1)}`, which will allow arbitrary-complexity base (-1) but only powers such as a constant or variable (1). For more tips, please see https://astroautomata.com/PySR/tuning/
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 2.010e+03
Head worker occupation: 5.4%
Progress: 84 / 120000 total iterations (0.070%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           4.054e-01  1.594e+01  y = wtheta
3           2.304e-03  2.585e+00  y = 0.98645 - sigma_th
5           1.491e-03  2.177e-01  y = (0.92529 ^ wtheta) - sigma_th
7           6.377e-04  4.245e-01  y = (1.6266 ^ (Mult + -0.46485)) - sigma_th
9           4.552e-04  1.686e-01  y = ((sigma_th ^ wtheta) ^ sigma_th) - (sigma_th ^ 1.4225)
11          3.233e-04  1.711e-01  y = ((0.62293 ^ wtheta) ^ (sigma_th ^ Mult)) - (sigma_th ^ 1.4...
                                  225)
---------------------------------------------------------------------------------------------------
Press 'q' and then <enter> to stop execution early.

Expressions evaluated per second: 2.230e+03
Head worker occupation: 5.3%
Progress: 206 / 

c:\Python\Python_3_11\Lib\site-packages\pysr\sr.py:65: UserWarning: You are using the `^` operator, but have not set up `constraints` for it. This may lead to overly complex expressions. One typical constraint is to use `constraints={..., '^': (-1, 1)}`, which will allow arbitrary-complexity base (-1) but only powers such as a constant or variable (1). For more tips, please see https://astroautomata.com/PySR/tuning/
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 2.860e+03
Head worker occupation: 9.3%
Progress: 123 / 120000 total iterations (0.102%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           7.761e-01  1.594e+01  y = sigma_th
3           2.404e-03  2.889e+00  y = 0.3063 ^ sigma_th
5           1.625e-03  1.959e-01  y = (0.95228 ^ wtheta) - sigma_th
7           8.264e-04  3.381e-01  y = 0.96947 - ((wtheta + 0.58185) * sigma_th)
9           4.269e-04  3.303e-01  y = ((0.20778 ^ sigma_th) / 1.0528) ^ (sigma_th + wtheta)
11          3.762e-04  6.322e-02  y = ((0.21805 ^ sigma_th) / (0.013222 + 1.0528)) ^ (wtheta + s...
                                  igma_th)
13          3.719e-04  5.696e-03  y = ((0.20106 ^ sigma_th) ^ (sigma_th + wtheta)) / ((2.7632 ^ ...
                                  0.077961) ^ wtheta)
15          3.343e-04  5.322e-02  y = ((0.20823 ^ sigma_th) ^ (wtheta + sigma_th)

c:\Python\Python_3_11\Lib\site-packages\pysr\sr.py:65: UserWarning: You are using the `^` operator, but have not set up `constraints` for it. This may lead to overly complex expressions. One typical constraint is to use `constraints={..., '^': (-1, 1)}`, which will allow arbitrary-complexity base (-1) but only powers such as a constant or variable (1). For more tips, please see https://astroautomata.com/PySR/tuning/
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 2.610e+03
Head worker occupation: 7.6%
Progress: 104 / 120000 total iterations (0.087%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           4.371e-01  1.594e+01  y = tau
3           2.304e-03  2.623e+00  y = 0.98819 - sigma_th
5           1.540e-03  2.015e-01  y = (0.54211 * Mult) ^ sigma_th
7           6.852e-04  4.048e-01  y = ((Mult + 0.49913) ^ 0.2887) - sigma_th
9           3.639e-04  3.163e-01  y = (0.56747 * Mult) + ((0.6438 - sigma_th) / 0.88562)
11          3.122e-04  7.670e-02  y = ((0.56747 ^ 0.92909) * Mult) + ((0.6438 - sigma_th) / 0.88...
                                  562)
15          3.092e-04  2.441e-03  y = ((0.65841 - sigma_th) / (1.123 ^ wtheta)) + ((0.56422 ^ 1....
                                  0705) * (Mult ^ 0.54928))
-------------------------------------------------------------------------------------------

c:\Python\Python_3_11\Lib\site-packages\pysr\sr.py:65: UserWarning: You are using the `^` operator, but have not set up `constraints` for it. This may lead to overly complex expressions. One typical constraint is to use `constraints={..., '^': (-1, 1)}`, which will allow arbitrary-complexity base (-1) but only powers such as a constant or variable (1). For more tips, please see https://astroautomata.com/PySR/tuning/
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 2.250e+03
Head worker occupation: 5.2%
Progress: 97 / 120000 total iterations (0.081%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.220e+00  1.594e+01  y = -0.17768
3           2.404e-03  3.115e+00  y = 0.30551 ^ sigma_th
5           2.030e-03  8.445e-02  y = (0.43321 * dTheta_dz) ^ sigma_th
7           9.360e-04  3.871e-01  y = (0.12608 ^ (sigma_th + wtheta)) ^ sigma_th
9           5.089e-04  3.046e-01  y = ((0.18974 ^ sigma_th) ^ (wtheta + sigma_th)) / 1.0352
11          3.998e-04  1.207e-01  y = (0.41857 * 0.4029) ^ ((sigma_th - -0.034941) * (sigma_th +...
                                   wtheta))
13          3.686e-04  4.066e-02  y = ((0.40404 * 0.79462) - 0.1266) ^ ((sigma_th - -0.034941) *...
                                   (sigma_th + wtheta))
15          3.643e-04  5.773e-03  y = ((0.79462 - 0.1548) / (2.0895 + 1.38

In [11]:
display(eqs_easy_mm)
display(eqs_medium_mm)
display(eqs_mediumhard_mm)
display(eqs_hard_mm)

complexity      loss     score  \
0           1  0.011007  0.000000   
1           3  0.002303  0.782138   
2           5  0.001490  0.217575   
3           7  0.000409  0.646504   
4           9  0.000288  0.175052   
5          11  0.000195  0.196357   
6          13  0.000194  0.002214   
7          15  0.000154  0.115435   

                                            equation  \
0                                          0.9217857   
1                              0.98740923 - sigma_th   
2                   (0.92444956 ^ wtheta) - sigma_th   
3        (1.7307163 - (0.5223851 ^ Mult)) - sigma_th   
4  (1.7683288 ^ (Mult + -0.4635251)) - (sigma_th ...   
5  ((0.53566545 + Mult) - (1.3816395 * sigma_th))...   
6  ((0.53566545 + Mult) - (1.3816395 * sigma_th))...   
7  ((0.53117687 + Mult) - (sigma_th * 1.3805505))...   

                                        sympy_format  \
0                                  0.921785700000000   
1                              0.98740923 - sigma_th   
2                      0.92444956**wtheta - sigma_th   
3            -0.5223851**Mult - sigma_th + 1.7307163   
4  1.7683288**(Mult - 0.4635251) - 1.177822590001...   
5  (Mult - 1.3816395*sigma_th + 0.53566545)**(Mul...   
6  (Mult - 1.3816395*sigma_th + 0.53566545)**(1.0...   
7  (Mult - 1.3805505*sigma_th + 0.53117687)**(1.3...   

                                       lambda_format  
0                 PySRFunction(X=>0.921785700000000)  
1             PySRFunction(X=>0.98740923 - sigma_th)  
2     PySRFunction(X=>0.92444956**wtheta - sigma_th)  
3  PySRFunction(X=>-0.5223851**Mult - sigma_th + ...  
4  PySRFunction(X=>1.7683288**(Mult - 0.4635251) ...  
5  PySRFunction(X=>(Mult - 1.3816395*sigma_th + 0...  
6  PySRFunction(X=>(Mult - 1.3816395*sigma_th + 0...  
7  PySRFunction(X=>(Mult - 1.3805505*sigma_th + 0...

complexity      loss     score  \
0           1  0.011007  0.000000   
1           3  0.002303  0.782138   
2           5  0.001490  0.217575   
3           7  0.000566  0.484111   
4           9  0.000329  0.271330   
5          11  0.000303  0.041779   
6          13  0.000286  0.027646   
7          15  0.000286  0.000128   

                                            equation  \
0                                         0.92177975   
1                               0.9874013 - sigma_th   
2                    (0.9244467 ^ wtheta) - sigma_th   
3     0.97286624 - (sigma_th ^ (1.5853751 - wtheta))   
4  ((0.24366201 ^ sigma_th) + -0.07427165) ^ (wth...   
5  ((0.5664766 ^ wtheta) - (sigma_th * 0.8879685)...   
6  ((0.21960822 ^ sigma_th) + -0.07427165) ^ ((wt...   
7  ((0.21960822 ^ sigma_th) + (-0.07427165 * 1.00...   

                                        sympy_format  \
0                                  0.921779750000000   
1                               0.9874013 - sigma_th   
2                       0.9244467**wtheta - sigma_th   
3        0.97286624 - sigma_th**(1.5853751 - wtheta)   
4  (0.24366201**sigma_th - 0.07427165)**(sigma_th...   
5  (0.5664766**wtheta - 0.8879685*sigma_th)**(sig...   
6  (0.21960822**sigma_th - 0.07427165)**(-sigma_2...   
7  (0.21960822**sigma_th - 0.074809295047185)**(-...   

                                       lambda_format  
0                 PySRFunction(X=>0.921779750000000)  
1              PySRFunction(X=>0.9874013 - sigma_th)  
2      PySRFunction(X=>0.9244467**wtheta - sigma_th)  
3  PySRFunction(X=>0.97286624 - sigma_th**(1.5853...  
4  PySRFunction(X=>(0.24366201**sigma_th - 0.0742...  
5  PySRFunction(X=>(0.5664766**wtheta - 0.8879685...  
6  PySRFunction(X=>(0.21960822**sigma_th - 0.0742...  
7  PySRFunction(X=>(0.21960822**sigma_th - 0.0748...

complexity      loss     score  \
0           1  0.011007  0.000000   
1           3  0.002303  0.782138   
2           5  0.001490  0.217575   
3           7  0.000414  0.640531   
4           9  0.000288  0.180571   
5          11  0.000195  0.196379   
6          13  0.000193  0.003549   
7          15  0.000154  0.113961   

                                            equation  \
0                                         0.92177784   
1                               0.9874083 - sigma_th   
2                    (0.9244497 ^ wtheta) - sigma_th   
3       (Mult + 0.6425511) * (0.90662134 - sigma_th)   
4  (1.7577951 ^ (Mult + -0.46466768)) - (sigma_th...   
5  ((Mult - -0.5361456) - (sigma_th / 0.7243437))...   
6  ((Mult - -0.5361456) - (sigma_th / 0.7264165))...   
7  ((Mult - -0.532812) - (sigma_th / 0.7264165)) ...   

                                        sympy_format  \
0                                  0.921777840000000   
1                               0.9874083 - sigma_th   
2                       0.9244497**wtheta - sigma_th   
3         (0.90662134 - sigma_th)*(Mult + 0.6425511)   
4  1.7577951**(Mult - 0.46466768) - 1.17098514277...   
5  (Mult - 1.3805600849431*sigma_th + 0.5361456)*...   
6  (Mult - 1.37662071277291*sigma_th + 0.5361456)...   
7  (Mult - 1.37662071277291*sigma_th + 0.532812)*...   

                                       lambda_format  
0                 PySRFunction(X=>0.921777840000000)  
1              PySRFunction(X=>0.9874083 - sigma_th)  
2      PySRFunction(X=>0.9244497**wtheta - sigma_th)  
3  PySRFunction(X=>(0.90662134 - sigma_th)*(Mult ...  
4  PySRFunction(X=>1.7577951**(Mult - 0.46466768)...  
5  PySRFunction(X=>(Mult - 1.3805600849431*sigma_...  
6  PySRFunction(X=>(Mult - 1.37662071277291*sigma...  
7  PySRFunction(X=>(Mult - 1.37662071277291*sigma...

complexity      loss     score  \
0           1  0.011007  0.000000   
1           3  0.002303  0.782139   
2           5  0.001490  0.217575   
3           7  0.000565  0.485010   
4           9  0.000329  0.270411   
5          11  0.000319  0.014917   
6          13  0.000261  0.100113   
7          15  0.000261  0.000538   

                                            equation  \
0                                         0.92178935   
1                               0.9874016 - sigma_th   
2                    (0.9244556 ^ wtheta) - sigma_th   
3      0.9719381 - (sigma_th ^ (1.5931371 - wtheta))   
4  ((0.243003 ^ sigma_th) + -0.074301824) ^ (sigm...   
5  (-0.06955985 + (0.24724236 ^ sigma_th)) ^ ((wt...   
6  ((sigma_2 * sigma_th) - -0.15872817) ^ ((sigma...   
7  ((sigma_2 * sigma_th) - (-0.15872817 * 0.98932...   

                                        sympy_format  \
0                                  0.921789350000000   
1                               0.9874016 - sigma_th   
2                       0.9244556**wtheta - sigma_th   
3         0.9719381 - sigma_th**(1.5931371 - wtheta)   
4  (0.243003**sigma_th - 0.074301824)**(sigma_th ...   
5  (0.24724236**sigma_th - 0.06955985)**(sigma_th...   
6  (sigma_2*sigma_th + 0.15872817)**((sigma_th + ...   
7  (sigma_2*sigma_th + 0.15703358805708)**((sigma...   

                                       lambda_format  
0                 PySRFunction(X=>0.921789350000000)  
1              PySRFunction(X=>0.9874016 - sigma_th)  
2      PySRFunction(X=>0.9244556**wtheta - sigma_th)  
3  PySRFunction(X=>0.9719381 - sigma_th**(1.59313...  
4  PySRFunction(X=>(0.243003**sigma_th - 0.074301...  
5  PySRFunction(X=>(0.24724236**sigma_th - 0.0695...  
6  PySRFunction(X=>(sigma_2*sigma_th + 0.15872817...  
7  PySRFunction(X=>(sigma_2*sigma_th + 0.15703358...

In [ ]:
df_coefs = pd.DataFrame(columns = ['File', 'Avg Ustar', 'Avg Tau', 'Ug', 'Q', 'RMSE', 'R2', 'C1', 'C2', 'C3'])

for item in selected_files:
    #file
    # print(item)
    ds_stat = nc.Dataset(os.path.join(path, item), mode='r')

    #ustar
    ustar = ds_stat.groups['default'].variables['ustar'][:]
    # print("Mean of ustar: ", np.mean(ustar))

    #tau
    grr = 9.8
    T_0 = 300
    beta = grr/T_0
    pbl_height = ds_stat.groups['thermo'].variables['zi'][:]
    wtheta_surface = ds_stat.groups['thermo']['th_flux'][:,0]  
    wstar = np.power( beta * (wtheta_surface) * pbl_height , 1/3) 
    tau = pbl_height/wstar
    # print("Mean of tau: ", np.mean(tau))

    #ug and q
    ug, q = extract_ug_q(item)
    # print("Ug: ", ug)
    # print("Q: ", q)

    #rmse, r2
    fitted_model, X_train, X_test, y_train, y_test, rmse, r2, coefficients = LES_linear_regressor(path, [item], 
                                                                                                  time_avg = 15, 
                                                                                                  indices = np.s_[:, 0:200], 
                                                                                                  verbose = False)
    
    #c1, c2, c3
    c1 = coefficients[0]
    c2 = coefficients[1]
    c3 = coefficients[2]

    # Create a new row to be appended
    new_row = {
        'File': item,
        'Avg Ustar': np.mean(ustar),
        'Avg Tau': np.mean(tau),
        'Ug': ug,
        'Q': q,
        'RMSE': rmse,
        'R2': r2,
        'C1': c1,
        'C2': c2,
        'C3': c3
    }

    # Append the new row to the DataFrame
    df_coefs = pd.concat([df_coefs, pd.DataFrame([new_row])], ignore_index=True)

    # print("")

In [ ]:
df_coefs['Inversion Strength'] = [4, 4, 4, 4, 2, 4, 3, 2, 3, 4, 4]
df_coefs['C1'] = df_coefs['C1']* df_coefs['Avg Tau']
df_coefs['C2'] = df_coefs['C2']/beta
df_coefs['C1'] = np.abs(df_coefs['C1'])
df_coefs['C2'] = np.abs(df_coefs['C2'])
df_coefs['C3'] = np.abs(df_coefs['C3'])

In [ ]:
df_coefs

In [ ]:
# Define the variables and their respective labels and colors
variables = ['Q', 'Ug', 'Avg Tau', 'Avg Ustar', 'Inversion Strength']
xlabels = ['Q', 'Ug', 'Avg Tau', 'Avg Ustar', 'SI']
titles = [
    'C1 (wtheta) Values in Relation to {}', 
    'C2 (theta2) Values in Relation to {}', 
    'C3 (multiply) Values in Relation to {}'
]
colors = ['red', 'green', 'blue']
columns = ['C1', 'C2', 'C3']

# Loop through each variable to create scatter plots
for var, xlabel in zip(variables, xlabels):
    plt.figure(figsize=(12, 4))
    
    for i, (col, color, title) in enumerate(zip(columns, colors, titles)):
        plt.subplot(1, 3, i + 1)
        plt.scatter(df_coefs[var], df_coefs[col], label=col, marker='o', color=color)
        plt.xlabel(xlabel)
        plt.ylabel(f'{col} Values')
        plt.title(title.format(xlabel))
        plt.legend()
    
    plt.tight_layout()
    plt.show()

# Special case for box plots for 'Inversion Strength'
plt.figure(figsize=(12, 4))

for i, col in enumerate(columns):
    plt.subplot(1, 3, i + 1)
    df_coefs.boxplot(column=col, by='Inversion Strength', grid=False, ax=plt.gca(), patch_artist=True)
    plt.xlabel('SI')
    plt.ylabel(f'{col} Values')
    plt.title(f'{col} (wtheta) Values in Relation to SI')
    plt.suptitle('')  # Suppress the automatic title

plt.tight_layout()
plt.show()


In [ ]:
###### Is there any relationship between fit and the forcings??? ################
plt.figure(figsize=(16, 4))

# Plot R2 vs. Q
plt.subplot(1, 4, 1)
plt.scatter(df_coefs['Q'], df_coefs['R2'], label='R2', marker='o', color='red')
plt.xlabel('Q')
plt.ylabel('R2 Values')
plt.title('R2 Values in Relation to Q')
plt.legend()

# Plot R2 vs. Ug
plt.subplot(1, 4, 2)
plt.scatter(df_coefs['Ug'], df_coefs['R2'], label='R2', marker='o', color='green')
plt.xlabel('Ug')
plt.ylabel('R2 Values')
plt.title('R2 Values in Relation to Ug')
plt.legend()

# Plot R2 vs. Avg Tau
plt.subplot(1, 4, 3)
plt.scatter(df_coefs['Avg Tau'], df_coefs['R2'], label='R2', marker='o', color='blue')
plt.xlabel('Avg Tau')
plt.ylabel('R2 Values')
plt.title('R2 Values in Relation to Avg Tau')
plt.legend()

# Plot R2 vs. Avg Ustar
plt.subplot(1, 4, 4)
plt.scatter(df_coefs['Avg Ustar'], df_coefs['R2'], label='R2', marker='o', color='darkmagenta')
plt.xlabel('Avg Ustar')
plt.ylabel('R2 Values')
plt.title('R2 Values in Relation to Avg Ustar')
plt.legend()

# Adjust layout to prevent overlap
plt.tight_layout()

# Show the plot
plt.show()


In [ ]:
###### Is there any relationship between fit and the forcings??? ################
plt.figure(figsize=(16, 4))

# Plot RMSE vs. Q
plt.subplot(1, 4, 1)
plt.scatter(df_coefs['Q'], df_coefs['RMSE'], label='RMSE', marker='o', color='red')
plt.xlabel('Q')
plt.ylabel('RMSE Values')
plt.title('RMSE Values in Relation to Q')
plt.legend()

# Plot RMSE vs. Ug
plt.subplot(1, 4, 2)
plt.scatter(df_coefs['Ug'], df_coefs['RMSE'], label='RMSE', marker='o', color='green')
plt.xlabel('Ug')
plt.ylabel('RMSE Values')
plt.title('RMSE Values in Relation to Ug')
plt.legend()

# Plot RMSE vs. Avg Tau
plt.subplot(1, 4, 3)
plt.scatter(df_coefs['Avg Tau'], df_coefs['RMSE'], label='RMSE', marker='o', color='blue')
plt.xlabel('Avg Tau')
plt.ylabel('RMSE Values')
plt.title('RMSE Values in Relation to Avg Tau')
plt.legend()

# Plot RMSE vs. Avg Ustar
plt.subplot(1, 4, 4)
plt.scatter(df_coefs['Avg Ustar'], df_coefs['RMSE'], label='RMSE', marker='o', color='purple')
plt.xlabel('Avg Ustar')
plt.ylabel('RMSE Values')
plt.title('RMSE Values in Relation to Avg Ustar')
plt.legend()

# Adjust layout to prevent overlap
plt.tight_layout()

# Show the plot
plt.show()


In [ ]:
# Define the variable pairs and their respective labels
variable_pairs = [
    ('Ug', 'Q'), 
    ('Ug', 'Avg Tau'), 
    ('Ug', 'Avg Ustar'), 
    ('Q', 'Avg Tau'), 
    ('Q', 'Avg Ustar'), 
    ('Avg Tau', 'Avg Ustar')
]

xlabel_pairs = [
    ('Q', 'Ug'), 
    ('Avg Tau', 'Ug'), 
    ('Avg Ustar', 'Ug'), 
    ('Avg Tau', 'Q'), 
    ('Avg Ustar', 'Q'), 
    ('Avg Ustar', 'Avg Tau')
]

# Function to create heatmap
def create_heatmap(ax, x_grid, y_grid, C, xlabel, ylabel, title):
    heatmap = ax.pcolormesh(x_grid, y_grid, C, shading='auto', cmap='viridis')
    ax.set_xlabel(xlabel)
    ax.set_ylabel(ylabel)
    ax.set_title(title)
    plt.colorbar(heatmap, ax=ax)

# Loop through each variable pair to create the plots
for (var1, var2), (xlabel, ylabel) in zip(variable_pairs, xlabel_pairs):
    # Pivot tables to create 2D arrays
    C1_grid = df_coefs.pivot_table(index=var1, columns=var2, values='C1')
    C2_grid = df_coefs.pivot_table(index=var1, columns=var2, values='C2')
    C3_grid = df_coefs.pivot_table(index=var1, columns=var2, values='C3')

    # Create a meshgrid for var1 and var2
    x_values = C1_grid.columns
    y_values = C1_grid.index
    x_grid, y_grid = np.meshgrid(x_values, y_values)

    # Plot the heatmaps
    fig, axes = plt.subplots(1, 3, figsize=(18, 5))

    create_heatmap(axes[0], x_grid, y_grid, C1_grid.values, xlabel, ylabel, f'Heatmap of C1 ({xlabel} vs {ylabel})')
    create_heatmap(axes[1], x_grid, y_grid, C2_grid.values, xlabel, ylabel, f'Heatmap of C2 ({xlabel} vs {ylabel})')
    create_heatmap(axes[2], x_grid, y_grid, C3_grid.values, xlabel, ylabel, f'Heatmap of C3 ({xlabel} vs {ylabel})')

    plt.tight_layout()
    plt.show()



In [ ]:
# Scatter plot of C2 and C3
plt.figure(figsize=(7, 4))
plt.scatter(df_coefs['C2'], df_coefs['C3'], marker='o', color='darkcyan', label='C2 vs C3')

# Adding labels and title
plt.xlabel('C2 Values')
plt.ylabel('C3 Values')
plt.title('Scatter Plot of C2 vs C3')
plt.legend()

# Show the plot
plt.show()


In [ ]:
df_coefs

In [ ]:
df_X_l = df_coefs[['Avg Ustar', 'Avg Tau', 'Ug', 'Q']]

#normalize the columns of df_X_l using the min max normalization
df_X_l = (df_X_l - df_X_l.min()) / (df_X_l.max() - df_X_l.min())

df_X_l = df_X_l.rename(columns={'Avg Ustar': 'Ustar', 'Avg Tau': 'Tau', 'Q': 'Q_ic'})
df_C1 = df_coefs['C1']
df_C2 = df_coefs['C2']
df_C3 = df_coefs['C3']

In [ ]:
df_X_l

In [ ]:
df_c1_eqs = discover_coef_eqs(df_X_l, df_C1)

In [ ]:
df_c1_eqs

In [ ]:
df_c2_eqs = discover_coef_eqs(df_X_l, df_C2)

In [ ]:
df_c2_eqs

In [ ]:
df_c3_eqs = discover_coef_eqs(df_X_l, df_C3)

In [ ]:
df_c3_eqs

- normalize the data, then do symbolic regression. see how well that works. 
- try both min max and z score normalization

- (maybe create jittered/noisy variables for better fit, look up how much paper needs)

other things to think abt: 
- ustar in front of third term (punished coefficient complexity) (think abt)
- parametrization for dwwtheta/dz

final presi will be: 
1. the problem (background on turbulence, atmospheric boundary layer, etc)
2. the methodology (PYSR, how does it work, genetic algorithms, etc)
3. Re-disovery of the original equation.
4. Current work on improving the parametrization.

Sara will decide how she wants us to present: Hopefully either all three, or Laura and Greta together and then me separate. 